In [ ]:
!pip install openai --quiet
!pip install langchain --quiet
!pip install cohere --quiet
!pip install tiktoken --quiet
!pip install langchain_community

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 303.0/303.0 kB 5.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.5/3.5 MB 49.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.5/2.5 MB 26.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 64.7/64.7 kB 4.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 50.9/50.9 kB 3.9 MB/s eta 0:00:00
  Attempting uninstall: requests
    Found existing installation: requests 2.32.4
    Uninstalling requests-2.32.4:
      Successfully uninstalled requests-2.32.4
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
google-colab 1.0.0 requires requests==2.32.4, but you have requests 2.32.5 which is incompatible.


In [ ]:
# @title
import os
os.environ['OPENAI_API_KEY'] = "Your own OPENAI_API_KEY"
os.environ['COHERE_API_KEY'] = "Your own COHERE_API_KEY"

#Better way
from google.colab import userdata
os.environ['OPENAI_API_KEY'] = userdata.get("OPENAI_API_KEY")
os.environ['COHERE_API_KEY'] = userdata.get("COHERE_API_KEY")

In [ ]:
# Helper function for printing docs


def pretty_print_docs(docs):
    print(
        f"\n{'-' * 100}\n".join(
            [f"Document {i+1}:\n\n" + d.page_content for i, d in enumerate(docs)]
        )
    )

# Step-1: Document Loading

In [ ]:
!pip install pypdf --quiet

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 323.5/323.5 kB 5.7 MB/s eta 0:00:00


In [ ]:
from langchain.document_loaders import PyPDFLoader

In [ ]:
!wget https://raw.githubusercontent.com/venkatareddykonasani/Datasets/master/Agreements/EMPLOYEE_AGREEMENT.pdf
loader = PyPDFLoader("EMPLOYEE_AGREEMENT.pdf")
pages = loader.load()
print(len(pages))

--2025-10-16 09:32:07--  https://raw.githubusercontent.com/venkatareddykonasani/Datasets/master/Agreements/EMPLOYEE_AGREEMENT.pdf
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 206079 (201K) [application/octet-stream]
Saving to: ‘EMPLOYEE_AGREEMENT.pdf’

EMPLOYEE_AGREEMENT. 100%[===================>] 201.25K  --.-KB/s    in 0.04s   

2025-10-16 09:32:08 (5.00 MB/s) - ‘EMPLOYEE_AGREEMENT.pdf’ saved [206079/206079]

13


In [ ]:
full_text =""
for page in pages:
  full_text += page.page_content

print("Pages", len(pages))
print("Lines" , len(full_text.split("\n")))
print("Words" , len(full_text.split(" ")))
print("Charecters", len(full_text))

Pages 13
Lines 369
Words 4204
Charecters 29540


# Step-2:Split the data into Chunks

In [ ]:
from langchain.text_splitter import RecursiveCharacterTextSplitter

In [ ]:
text_splitter = RecursiveCharacterTextSplitter(chunk_size=300, chunk_overlap=30)
chunks = text_splitter.split_documents(pages)
print(len(chunks))

133


In [ ]:
print(chunks[0])

page_content='EX-10.1 3 smtp_ex10z1.htm EMPLOYEE AGREEMENT
EXHIBIT 10.1
EMPLOYEE AGREEMENT
THIS EMPLOYEE AGREEMENT made as of September___, 2014, by and between SharpSpring,
Inc., a Delaware corporation (the “Company”), whose principal place of business is at 802 NW 5th Avenue,' metadata={'producer': 'Skia/PDF m123', 'creator': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/123.0.0.0 Safari/537.36', 'creationdate': '2024-04-03T12:51:00+00:00', 'title': 'EMPLOYEE AGREEMENT', 'moddate': '2024-04-03T12:51:00+00:00', 'source': 'EMPLOYEE_AGREEMENT.pdf', 'total_pages': 13, 'page': 0, 'page_label': '1'}


# Step-3: Creating embeddings

In [ ]:
from langchain.embeddings import OpenAIEmbeddings, CohereEmbeddings

In [ ]:
#embeddings = OpenAIEmbeddings()
embeddings = CohereEmbeddings(user_agent="langchain")

/tmp/ipython-input-1256318641.py:2: LangChainDeprecationWarning: The class `CohereEmbeddings` was deprecated in LangChain 0.0.30 and will be removed in 1.0. An updated version of the class exists in the :class:`~langchain-cohere package and should be used instead. To use it run `pip install -U :class:`~langchain-cohere` and import as `from :class:`~langchain_cohere import CohereEmbeddings``.
  embeddings = CohereEmbeddings(user_agent="langchain")


In [ ]:
# A sample embedding

sample_embedding = embeddings.embed_query("You must follow the rules")
print(sample_embedding)

[0.9038086, 0.22033691, -1.1132812, 0.87109375, 0.7758789, -0.8671875, -1.7265625, -3.4882812, -0.79785156, -0.9248047, 0.7158203, 0.12878418, -2.1992188, -1.4003906, 1.71875, -2.2148438, 1.2626953, 3.6875, 1.5859375, -0.8857422, 0.65478516, 0.81152344, 0.47265625, 0.39990234, 3.5410156, -0.4165039, 2.3496094, -2.7578125, -1.3652344, 0.9609375, 0.051849365, 0.72753906, 0.89208984, 1.8652344, -1.4140625, -1.7783203, 2.2910156, -0.8955078, -0.10760498, 1.2958984, -2.4003906, 1.0673828, 0.12963867, -1.7050781, 2.0976562, -1.7285156, -1.3632812, 3.1933594, 1.6357422, -0.96875, 2.4628906, 0.27783203, -0.42333984, 0.7553711, -0.7441406, -1.8066406, -3.5625, -0.84472656, -0.5419922, -0.30029297, -0.28881836, -0.79052734, 1.1015625, -1.3984375, 0.3618164, -1.7236328, -1.6503906, -1.9824219, 0.1928711, 0.72753906, 0.18774414, 1.8144531, 2.2539062, -0.56347656, 0.27514648, 1.2304688, -1.4589844, 1.5078125, 0.4831543, -1.9550781, -0.82128906, 0.85302734, -1.2285156, 1.2070312, -1.0117188, -1.3183

In [ ]:
len(sample_embedding)

4096

In [ ]:
sample_docs=["You must follow the rules",
            "You must not disclose the rules"]

embeded_vectors1= embeddings.embed_documents(sample_docs)
print(embeded_vectors1)

[[0.9038086, 0.22033691, -1.1132812, 0.87109375, 0.7758789, -0.8671875, -1.7265625, -3.4882812, -0.79785156, -0.9248047, 0.7158203, 0.12878418, -2.1992188, -1.4003906, 1.71875, -2.2148438, 1.2626953, 3.6875, 1.5859375, -0.8857422, 0.65478516, 0.81152344, 0.47265625, 0.39990234, 3.5410156, -0.4165039, 2.3496094, -2.7578125, -1.3652344, 0.9609375, 0.051849365, 0.72753906, 0.89208984, 1.8652344, -1.4140625, -1.7783203, 2.2910156, -0.8955078, -0.10760498, 1.2958984, -2.4003906, 1.0673828, 0.12963867, -1.7050781, 2.0976562, -1.7285156, -1.3632812, 3.1933594, 1.6357422, -0.96875, 2.4628906, 0.27783203, -0.42333984, 0.7553711, -0.7441406, -1.8066406, -3.5625, -0.84472656, -0.5419922, -0.30029297, -0.28881836, -0.79052734, 1.1015625, -1.3984375, 0.3618164, -1.7236328, -1.6503906, -1.9824219, 0.1928711, 0.72753906, 0.18774414, 1.8144531, 2.2539062, -0.56347656, 0.27514648, 1.2304688, -1.4589844, 1.5078125, 0.4831543, -1.9550781, -0.82128906, 0.85302734, -1.2285156, 1.2070312, -1.0117188, -1.318

In [ ]:
print(len(embeded_vectors1))
print(len(embeded_vectors1[0]))

2
4096


In [ ]:
print(sample_embedding)
print(embeded_vectors1[0])

[0.9038086, 0.22033691, -1.1132812, 0.87109375, 0.7758789, -0.8671875, -1.7265625, -3.4882812, -0.79785156, -0.9248047, 0.7158203, 0.12878418, -2.1992188, -1.4003906, 1.71875, -2.2148438, 1.2626953, 3.6875, 1.5859375, -0.8857422, 0.65478516, 0.81152344, 0.47265625, 0.39990234, 3.5410156, -0.4165039, 2.3496094, -2.7578125, -1.3652344, 0.9609375, 0.051849365, 0.72753906, 0.89208984, 1.8652344, -1.4140625, -1.7783203, 2.2910156, -0.8955078, -0.10760498, 1.2958984, -2.4003906, 1.0673828, 0.12963867, -1.7050781, 2.0976562, -1.7285156, -1.3632812, 3.1933594, 1.6357422, -0.96875, 2.4628906, 0.27783203, -0.42333984, 0.7553711, -0.7441406, -1.8066406, -3.5625, -0.84472656, -0.5419922, -0.30029297, -0.28881836, -0.79052734, 1.1015625, -1.3984375, 0.3618164, -1.7236328, -1.6503906, -1.9824219, 0.1928711, 0.72753906, 0.18774414, 1.8144531, 2.2539062, -0.56347656, 0.27514648, 1.2304688, -1.4589844, 1.5078125, 0.4831543, -1.9550781, -0.82128906, 0.85302734, -1.2285156, 1.2070312, -1.0117188, -1.3183

# Step-4: Storing in Vector Stores

In [ ]:
!pip install chromadb -q

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 67.3/67.3 kB 2.0 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 19.9/19.9 MB 91.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 278.2/278.2 kB 23.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 82.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 103.3/103.3 kB 9.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 17.4/17.4 MB 91.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 72.5/72.5 kB 6.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 132.3/132.3 kB 12.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 65.9/65.9 kB 3.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 208.0/208.0 kB 17.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 105.4/105.4 kB 8.7 MB/s eta

In [ ]:
from langchain.vectorstores import Chroma

In [ ]:
emp_rules_db= Chroma.from_documents(chunks,
                                    embeddings,
                                    persist_directory="emp_rules_db"
                          )
emp_rules_db.persist()
#persist() stores teh DB Locally on Hard-disk insted of RAM

/tmp/ipython-input-2299136942.py:5: LangChainDeprecationWarning: Since Chroma 0.4.x the manual persistence method is no longer supported as docs are automatically persisted.
  emp_rules_db.persist()


# Step-5: Retrieval

In [ ]:
retriever = emp_rules_db.as_retriever()
result=retriever.get_relevant_documents("What is the policy for sick leaves")
result

/tmp/ipython-input-4044122518.py:2: LangChainDeprecationWarning: The method `BaseRetriever.get_relevant_documents` was deprecated in langchain-core 0.1.46 and will be removed in 1.0. Use :meth:`~invoke` instead.
  result=retriever.get_relevant_documents("What is the policy for sick leaves")


[Document(metadata={'source': 'EMPLOYEE_AGREEMENT.pdf', 'creator': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/123.0.0.0 Safari/537.36', 'creationdate': '2024-04-03T12:51:00+00:00', 'title': 'EMPLOYEE AGREEMENT', 'moddate': '2024-04-03T12:51:00+00:00', 'page': 1, 'producer': 'Skia/PDF m123', 'page_label': '2', 'total_pages': 13}, page_content='sick days and personal absence days as authorized by the Company for its other employees.\nARTICLE 6\nFringe Benefits\nEmployee shall be entitled to participate in and receive benefits from all of the Company’s employee\nbenefit plans that are now, or in the future may be, maintained by the'),
 Document(metadata={'page': 1, 'title': 'EMPLOYEE AGREEMENT', 'creator': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/123.0.0.0 Safari/537.36', 'source': 'EMPLOYEE_AGREEMENT.pdf', 'page_label': '2', 'creationdate': '2024-04-03T12:51:00+00:00', 'moddate': '2024-04-03T12:

In [ ]:
for i in range(len(result)):
  print(result[i].metadata)

{'source': 'EMPLOYEE_AGREEMENT.pdf', 'creator': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/123.0.0.0 Safari/537.36', 'creationdate': '2024-04-03T12:51:00+00:00', 'title': 'EMPLOYEE AGREEMENT', 'moddate': '2024-04-03T12:51:00+00:00', 'page': 1, 'producer': 'Skia/PDF m123', 'page_label': '2', 'total_pages': 13}
{'page': 1, 'title': 'EMPLOYEE AGREEMENT', 'creator': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/123.0.0.0 Safari/537.36', 'source': 'EMPLOYEE_AGREEMENT.pdf', 'page_label': '2', 'creationdate': '2024-04-03T12:51:00+00:00', 'moddate': '2024-04-03T12:51:00+00:00', 'producer': 'Skia/PDF m123', 'total_pages': 13}
{'title': 'EMPLOYEE AGREEMENT', 'page': 1, 'producer': 'Skia/PDF m123', 'source': 'EMPLOYEE_AGREEMENT.pdf', 'page_label': '2', 'creationdate': '2024-04-03T12:51:00+00:00', 'creator': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/123.0.0.0 Safa

You can also set a retrieval method that sets a similarity score threshold and only returns documents with a score above that threshold.


### pretty_print_docs

In [ ]:
retriever = emp_rules_db.as_retriever()
result=retriever.get_relevant_documents("What is the policy for insurance?")
pretty_print_docs(result)

Document 1:

Company for its employees, including, without limitation, the Company’s health insurance plan. No amounts
paid to Employee from an employee benefit plan shall count as compensation due Employee as base salary or
----------------------------------------------------------------------------------------------------
Document 2:

shareholders, officers, directors, employees, counsel, agents, affiliates and assigns (collectively, the
“Company Indemnities”) harmless from and against any and all direct or indirect demands, claims,
----------------------------------------------------------------------------------------------------
Document 3:

remedies available to the Company with respect to Employee’s breach of his obligations hereunder,
Employee shall defend, indemnify and hold the Company, the Affiliates, and each of their respective
----------------------------------------------------------------------------------------------------
Document 4:

shall promptly pay or reimburse E

In [ ]:
for i in range(len(result)):
  print(result[i].metadata)

{'page': 2, 'page_label': '3', 'creationdate': '2024-04-03T12:51:00+00:00', 'producer': 'Skia/PDF m123', 'total_pages': 13, 'title': 'EMPLOYEE AGREEMENT', 'creator': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/123.0.0.0 Safari/537.36', 'moddate': '2024-04-03T12:51:00+00:00', 'source': 'EMPLOYEE_AGREEMENT.pdf'}
{'moddate': '2024-04-03T12:51:00+00:00', 'total_pages': 13, 'title': 'EMPLOYEE AGREEMENT', 'page_label': '7', 'creator': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/123.0.0.0 Safari/537.36', 'producer': 'Skia/PDF m123', 'creationdate': '2024-04-03T12:51:00+00:00', 'page': 6, 'source': 'EMPLOYEE_AGREEMENT.pdf'}
{'page_label': '7', 'creator': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/123.0.0.0 Safari/537.36', 'creationdate': '2024-04-03T12:51:00+00:00', 'total_pages': 13, 'source': 'EMPLOYEE_AGREEMENT.pdf', 'moddate': '2024-04-03T12:51:00+00:00', 

In [ ]:
retriever = emp_rules_db.as_retriever()
result=retriever.get_relevant_documents("Employee Monthly Salary ")
pretty_print_docs(result)

Document 1:

Compensation of Employee
4.1. Base Compensation.  For all services rendered by Employee under this Employee Agreement, the
Company agrees to pay Employee the rate of $14,583 per month (the “base salary”), which shall be payable
----------------------------------------------------------------------------------------------------
Document 2:

to Employee not less frequently than bi-monthly, or as is consistent with the Company’s practice for its other
employees.  
4.2. Other Compensation.  Employee shall receive other compensation as more fully described on
Appendix B, attached hereto and made a part hereof.
----------------------------------------------------------------------------------------------------
Document 3:

Company for its employees, including, without limitation, the Company’s health insurance plan. No amounts
paid to Employee from an employee benefit plan shall count as compensation due Employee as base salary or
------------------------------------------------

In [ ]:
for i in range(len(result)):
  print(result[i].metadata)

{'creationdate': '2024-04-03T12:51:00+00:00', 'producer': 'Skia/PDF m123', 'total_pages': 13, 'creator': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/123.0.0.0 Safari/537.36', 'source': 'EMPLOYEE_AGREEMENT.pdf', 'page': 1, 'page_label': '2', 'title': 'EMPLOYEE AGREEMENT', 'moddate': '2024-04-03T12:51:00+00:00'}
{'title': 'EMPLOYEE AGREEMENT', 'page': 1, 'creationdate': '2024-04-03T12:51:00+00:00', 'moddate': '2024-04-03T12:51:00+00:00', 'producer': 'Skia/PDF m123', 'source': 'EMPLOYEE_AGREEMENT.pdf', 'page_label': '2', 'creator': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/123.0.0.0 Safari/537.36', 'total_pages': 13}
{'total_pages': 13, 'title': 'EMPLOYEE AGREEMENT', 'creator': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/123.0.0.0 Safari/537.36', 'moddate': '2024-04-03T12:51:00+00:00', 'source': 'EMPLOYEE_AGREEMENT.pdf', 'creationdate': '2024-04-03T12:51

# RAG Example-2

In [ ]:
# Step-1:Document Loading
from langchain.document_loaders import PyPDFLoader
!wget https://raw.githubusercontent.com/venkatareddykonasani/Datasets/master/Banking_System_Doc/BASEL.pdf
loader = PyPDFLoader("BASEL.pdf")
pages = loader.load()
print(len(pages))

--2025-10-16 09:34:07--  https://raw.githubusercontent.com/venkatareddykonasani/Datasets/master/Banking_System_Doc/BASEL.pdf
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.109.133, 185.199.110.133, 185.199.108.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.109.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1260197 (1.2M) [application/octet-stream]
Saving to: ‘BASEL.pdf’

BASEL.pdf           100%[===================>]   1.20M  --.-KB/s    in 0.08s   

2025-10-16 09:34:07 (14.7 MB/s) - ‘BASEL.pdf’ saved [1260197/1260197]

77


In [ ]:
#Step-2:Split the data into Chunks

from langchain.text_splitter import RecursiveCharacterTextSplitter
text_splitter = RecursiveCharacterTextSplitter(chunk_size=500, chunk_overlap=50)
chunks = text_splitter.split_documents(pages)
print(len(chunks))

521


In [ ]:
#Step-3: Creating Embeddings
from langchain.embeddings import OpenAIEmbeddings, CohereEmbeddings
#embeddings = OpenAIEmbeddings()
embeddings = CohereEmbeddings(user_agent="langchain")

#Step-4: Storing in a Vector DB
#!rm -rf basel_norms_db
basel_norms_db= Chroma.from_documents(chunks,
                                    embeddings,
                                    persist_directory="basel_norms_db"
                          )
basel_norms_db.persist()

In [ ]:
#Step-5 Retrieval

retriever = basel_norms_db.as_retriever()
result=retriever.get_relevant_documents("What percentage is the minimum Capital Requirements")
print(result)
print(len(result))
print([i.metadata for i in result])

[Document(metadata={'agenda item1': '', 'page': 67, 'description0': '', 'sort order': '0.110000000000000', 'total_pages': 77, 'doc #': '', 'comments': '', 'producer': 'Acrobat Distiller 9.4.0 (Windows)', 'company': '', 'keywords': '', 'meeting': '2010 - 138th Meeting of the BCBS November-December 2010', 'author': 'Basel Committee on Banking Supervision', 'source': 'BASEL.pdf', 'contenttype': 'Document', 'creationdate': '2011-05-31T11:52:06+02:00', 'subject': 'Full text of "Basel III: A global regulatory framework for more resilient banks and banking systems - post BCBS meeting - revised version", June 2011', 'title': 'Basel III: A global regulatory framework for more resilient banks and banking systems - post BCBS meeting - revised version June 2011', 'moddate': '2019-11-14T17:33:29+01:00', 'page_label': '68', 'creator': 'Acrobat PDFMaker 9.1 for Word'}, page_content='capital) \nMinimum Capital Conservation Ratios \n(expressed as a percentage of earnings) \n4.5% -  5.75% 100% \n>5.75% 

In [ ]:
retriever = basel_norms_db.as_retriever()
result=retriever.get_relevant_documents("What are PD and LGD")
print(result)
print(len(result))
print([i.metadata for i in result])

[Document(metadata={'title': 'Basel III: A global regulatory framework for more resilient banks and banking systems - post BCBS meeting - revised version June 2011', 'doc #': '', 'page_label': '7', 'moddate': '2019-11-14T17:33:29+01:00', 'author': 'Basel Committee on Banking Supervision', 'contenttype': 'Document', 'keywords': '', 'sort order': '0.110000000000000', 'description0': '', 'producer': 'Acrobat Distiller 9.4.0 (Windows)', 'meeting': '2010 - 138th Meeting of the BCBS November-December 2010', 'agenda item1': '', 'creator': 'Acrobat PDFMaker 9.1 for Word', 'company': '', 'comments': '', 'page': 6, 'creationdate': '2011-05-31T11:52:06+02:00', 'source': 'BASEL.pdf', 'total_pages': 77, 'subject': 'Full text of "Basel III: A global regulatory framework for more resilient banks and banking systems - post BCBS meeting - revised version", June 2011'}, page_content='LCR  Liquidity Coverage Ratio \nLGD  Loss given default \nMtM  Mark-to-market \nNSFR  Net Stable Funding Ratio \nOBS  Off